In [1]:
import thinkdsp
import pygame,easygui
import winsound
import pickle
def sample_generator():
    #The Wave is Segmentet into Sequences (0.1 sec)
    GotIt = False
    while not GotIt :
        try :
            M_Name = easygui.enterbox("Enter .wav File(Name)","Music Import")
            M_Name = "Music/"+M_Name
            if not ".wav" in M_Name :

                M_Name += ".wav"
            wave = thinkdsp.read_wave(M_Name)
            GotIt = True
        except:
            easygui.msgbox("Failed to load wav-File","Loading Error")
    start = 0.0
    Cash = []
    Cash2 = []
    Meng = 0
    while start < wave.duration:
        segment = wave.segment(start, 0.1)
        if segment.duration > 0:
            Meng += 1
            spectrum = segment.make_spectrum()
            Cash.append(spectrum)
            Cash2.append(segment)
        start += 0.1
    SaveData(Cash,M_Name)
    return Cash,Cash2,Meng,M_Name

In [2]:
def SaveData(Specs,M_Name):
    #Setup Vars 
    FinalData = [M_Name]
    #Ask for User input
    if easygui.ynbox("Do you want to save the Data to external File? \n WARNING : may generate extrem big files","Save?"):
        #Open file
        SaveFile = open("Saves/SaveFile.maz","wb")
        #Process every Datapack
        for spectrum in Specs :
            #Do the Math
            Bars = []
            D = 0.6
            S = 1
            fs,amps = spectrum.render_full()
            RAMPD = []
            ID = -1
            for PosX in fs :
                ID += 1
                if (PosX*D) < screen.get_width():
                    AMPD = (amps[ID]+1)*2
                    RAMPD.append(AMPD)
            print(RAMPD)
            FinalData.append(RAMPD)
        #Save Data to .maz save-File
        pickle.dump(FinalData,SaveFile)
        SaveFile.close()

In [3]:
def GraphDraw(Freq_List):
    SCREENHEIGHT = screen.get_height()
    Itera = 0
    HEIGH = 0
    for Var in Freq_List :
        if Var > HEIGH :
            HEIGH = Var
    for Item in Freq_List :
        try :
            pygame.draw.line(screen,Time_Color[Time_ID-1],Old,[Itera*5,(SCREENHEIGHT-HEIGH)+Item],3)
        except :
            pass
        Old = [Itera*5,(SCREENHEIGHT-HEIGH)+Item]
        Itera += 1
    

In [4]:
def Render(screen,Bars,fs):
    global Peak_List,NPeak_List
    #Peak Scanner
    SID = -1
    GR = 0
    SM = 10000
    GrID = 0
    for Bar in Bars :
            SID += 1
            if Bar[3] > GR :
                GR = Bar[3]
                GrID = SID
                Hfs = fs[GrID]
            if Bar[3] < SM :
                SM = Bar[3]
                GrID2 = SID
    Peak_List.append(Hfs/12)
    NPeak_List.append(SM*30)
    if len(Peak_List) >= screen.get_width()/5 :
        Peak_List = Peak_List[1:]
    if len(NPeak_List) >= screen.get_width()/5 :
        NPeak_List = NPeak_List[1:]
    #Main Render
    D = 5
    Len = len(Bars)
    global Epics_Cash
    ID = -1
    #Blue Line 
    if Line_Aktiv :
        for Bar in Bars :
            try :
                pygame.draw.line(screen,[0,100,100],Graph,[Bar[0]-1,Bar[3]+30],3)
                pygame.draw.line(screen,[0,100,100],[Bar[0]-1,Bar[3]+30],[Bar[0]+D+1,Bar[3]+30],3)
            except :
                pass
            Graph = [Bar[0]+D+1,Bar[3]+30] 
    #Graph
    if Bar_Aktiv :
        for Bar in Bars :
            ID += 1
            if Effects_Aktiv :
                if ID == Epics_Cash[0]:
                    pygame.draw.rect(screen,Epics_Cash[3],Bar)
                elif ID-1 == Epics_Cash[0] or ID+1 == Epics_Cash[0]:
                    pygame.draw.rect(screen,Epics_Cash[2],Bar)
                else :
                    pygame.draw.rect(screen,Epics_Cash[1],Bar)
            else :
                pygame.draw.rect(screen,Epics_Cash[1],Bar)
            if ID == GrID :
                pygame.draw.rect(screen,[255,0,0],Bar)
            if ID == GrID2 :
                pygame.draw.rect(screen,[0,0,255],Bar)
        Epics_Cash[0] += 1
        if Epics_Cash[0] >= Len :
            Epics_Cash[0] = 0
        #pygame.draw.rect(screen,[255,255,255],[0,10,800,10],False)
    #AverageLine
    Av = 0
    Avid = 0
    global Freq_List
    for Bar in Bars :
        Avid
        Av += Bar[3]
        Avid += 1
        if len(Freq_List) >= screen.get_width()/5 :
            Freq_List = Freq_List[1:]
    Av = int(Av/Avid)
    Freq_List.append(Av)
    if Av_Aktiv :
        pygame.draw.line(screen,[0,100,0],[0,Av],[screen.get_width(),Av],3)
    if Time_Aktiv :
        if Time_ID == 1 :
            GraphDraw(Freq_List) 
        elif Time_ID == 2 :
            GraphDraw(Peak_List) 
        elif Time_ID == 3 :
            GraphDraw(NPeak_List) 
    #PeakFont
    if Pfont_Aktiv :
        font = pygame.font.SysFont("Arial",20)
        Img = font.render(str(Hfs), True,[255,255,255])
        screen.blit(Img,[700,600])

In [5]:
pygame.init()
def NextData(Cash):
    #Reurns the current Sample
    Ret = Cash[Itera[1]]
    Itera[1] += 1
    if Itera[1] == Iteralen[1]-1:
        Itera[1] = 0
    return Ret,Cash
def Update(screen,spectrum):
    #Bar ot Graph/Data
    Bars = []
    D = 0.6
    S = 1
    fs,amps = spectrum.render_full()
    RAMPD = []
    ID = -1
    for PosX in fs :
        ID += 1
        if (PosX*D) < screen.get_width():
            AMPD = (amps[ID]+1)*2
            Block = 50
            RAMPD.append(AMPD)
            if AMPD >= 700 :
                AMPD = 700
            Bars.append([PosX*D,0,5,AMPD])
    Render(screen,Bars,fs)



In [6]:
def UpdateM2(screen,spectrum):
    global DisplayFont
    #Display Crazy Numbers aka. the raw amps. Data in shorted form (Not everything fits on one screen line)
    Data = []
    D = 0.6
    S = 1
    fs,amps = spectrum.render_full()
    for item in amps[:70] :
        Data.append(round(item,2))
    font = pygame.font.SysFont("Arial",10)
    DisplayFont.append(font.render(str(Data), True,[0,255,0]))
    if len(DisplayFont) > 35:
        DisplayFont = DisplayFont[1:]
    for Enu,Obj in enumerate(DisplayFont) :
        screen.blit(Obj,[0,Enu*20])

In [7]:
#Setup
#screen = pygame.display.set_mode([1920,1080],pygame.RESIZABLE)
screen = pygame.display.set_mode([1280,720])
#VarDef
Freq_List = []
Peak_List = []
NPeak_List = []
Time_Color = [[0,100,0],[100,0,0],[0,0,100]]
Vol = 1
Aktiv = True
uhr = pygame.time.Clock()
Music_Name = ""
Mode = easygui.choicebox("Display Mode:(only Normal mode is intendet the other two are just a test/gag and may cause lags.)","Choose View Mode",["Normal","HackedData","RamKiller"])
if Mode == "RamKiller":
    easygui.msgbox("This mode is too slow, please do not ues it if you want somethink that is sync. to the music.","WARNING")
Cash,Cash2,Meng,M_Name =sample_generator()
easygui.msgbox(str(Meng)+" Samples,Sample-duration : 0.1 sec."+",length: "+str(int(Meng/10)),"Music Data")
Cash2B = Cash2[:]
CashCopy = Cash[:]
Epics_Cash = [0,[255,255,255],[200,255,200],[0,255,0]]
Itera = [0,0]
Iteralen = [len(Cash2),len(Cash)]
#Pygame Mixer Start
M_Type = "STD"
if M_Type == "STD":
    pygame.mixer.music.load(M_Name)
    pygame.mixer.music.set_volume(Vol)
    pygame.mixer.music.play(-1)
#Pygame setup
screen.fill([0,0,0])
pygame.key.set_repeat(80,100)
#Feature Var
Bar_Aktiv = True
Line_Aktiv = True
Av_Aktiv = True
Pfont_Aktiv = True
KeyKill = False
Runtime = 0
Restart = False
Time_Aktiv = True
Effects_Aktiv = False
Time_ID = 0
Playsound = 0
#Test
OldSound = 10
DisplayFont = []
#Generate Massiv amounds of Lists if needed (For RamKiller mode)
if Mode == "RamKiller" :
    for ID in range(0,len(Cash[0].render_full()[1])):
        exec("DataBit"+str(ID)+" = []")

[0]


In [8]:
#%%capture
spectrum,Cash = NextData(Cash)
#Main Loop
while Aktiv :
    uhr.tick(10)
    spectrum,Cash = NextData(Cash)
    #Play Music/Timer
    if M_Type == "STD":
        if not Restart:
            Restart = False
        Runtime = Itera[1]/10
        if spectrum != None:
            screen.fill([0,0,0])
            if Mode == "Normal":
                Update(screen,spectrum)
            elif Mode == "HackedData" :
                UpdateM2(screen,spectrum)
            elif Mode == "RamKiller" :
                #Create a gigantic Graph plotting every frequency (Uses mutch RAM Storrage)
                for ID,Item in enumerate(spectrum.render_full()[1]) :
                    Db = eval("DataBit"+str(ID))
                    Db.append([-10,Item*1000])
                    if len(Db) > 128:
                        exec("DataBit"+str(ID)+" = Db[1:]")
                    for Item in Db :
                        Item[0] += 10
                    try :
                        pygame.draw.lines(screen,[ID,ID,ID],False,Db,2)
                    except :
                        pass
                pygame.display.flip()
        Itera[0]+=1
    if M_Type == "SAMP":
        ToSound = Cash2[Itera[0]]
        ToSound.play("sound.wav")
        winsound.PlaySound('sound.wav', winsound.SND_FILENAME)
        #pygame.mixer.music.load("sound.wav")
        #pygame.mixer.music.set_volume(Vol)
        #pygame.mixer.music.play(1)
        Itera[0]+=1
        if spectrum != None:
            screen.fill([0,0,0]) 
            Update(screen,spectrum)
        Runtime = Itera[1]/10
    if Itera[0] == Iteralen[0]-1:
        Itera[0] = 0
        #Restart Music
        Restart = True
    else :
        Cash = CashCopy
    if Itera[1] == 0 :
        Runtime = 0
    #Runtime-Anzeige
    font = pygame.font.SysFont("Arial",20)
    Runtime2 = int(Runtime)
    Img = font.render("Runtime(Sec): "+str(Runtime2), True,[255,255,255])
    screen.blit(Img,[1000,600])
    #Main event Loop
    pygame.display.flip()
    for event in pygame.event.get():
        if event.type == pygame.QUIT :
            Aktiv = False
        elif event.type == pygame.KEYDOWN :
            #Key Handler
            if event.key == pygame.K_b :
                Bar_Aktiv = not Bar_Aktiv
            elif event.key == pygame.K_l :
                Line_Aktiv = not Line_Aktiv
            elif event.key == pygame.K_a :
                Av_Aktiv = not Av_Aktiv
            elif event.key == pygame.K_f :
                Pfont_Aktiv = not Pfont_Aktiv
            elif event.key == pygame.K_t :
                Time_ID += 1
                if Time_ID > 3 :
                    Time_ID = 0
            elif event.key == pygame.K_e :
                Effects_Aktiv = not Effects_Aktiv
            #Sound
            elif event.key == pygame.K_UP :
                Vol += 0.1
                pygame.mixer.music.set_volume(Vol)
            elif event.key == pygame.K_DOWN :
                Vol -= 0.1
                pygame.mixer.music.set_volume(Vol)
            #else :
                #Aktiv = False
                #KeyKill = True
pygame.quit()

1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3


5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5


7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7


9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9
9


...

129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129


129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129


129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129


129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129


129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129
129


In [9]:
if KeyKill :
    easygui.msgbox("Killed by KeyInterupt","System Shutdown")